# 01_02_move_fits_files_using_keyword

## 필요한 모듈

이 프로젝트를 위해서는 아래의 모듈이 필요하다. 

> numpy, pandas, matplotlib, astropy, version_information

### 모듈 설치

1. 콘솔 창에서 모듈을 설치할 때는 아래와 같은 형식으로 입력하면 된다.

>pip install module_name==version

>conda install module_name=version

2. 주피터 노트북(코랩 포함)에 설치 할 때는 아래의 셀을 실행해서 실행되지 않은 모듈을 설치할 수 있다. (pip 기준) 만약 아나콘다 환경을 사용한다면 7행을 콘다 설치 명령어에 맞게 수정하면 된다.

In [51]:
#import sys
#!pip install astropy==5.2 photutils==1.6 #astroscrappy==1.1.1
#%pip install astroscrappy==1.1.1

In [52]:
import importlib, sys, subprocess
packages = "numpy, pandas, matplotlib, scipy, astropy, photutils, ccdproc, astroscrappy, version_information" # required modules
pkgs = packages.split(", ")
for pkg in pkgs :
    if not importlib.util.find_spec(pkg):
        #print(f"**** module {pkg} is not installed")
        subprocess.check_call([sys.executable, '-m', 'pip', 'install', pkg, '-q'])
    else: 
        print(f"**** module {pkg} is installed")

%load_ext version_information
import time
now = time.strftime("%Y-%m-%d %H:%M:%S (%Z = GMT%z)")
print(f"This notebook was generated at {now} ")

vv = %version_information {packages}
for i, pkg in enumerate(vv.packages):
    print(f"{i} {pkg[0]:10s} {pkg[1]:s}")

**** module numpy is installed
**** module pandas is installed
**** module matplotlib is installed
**** module scipy is installed
**** module astropy is installed
**** module photutils is installed
**** module ccdproc is installed
**** module astroscrappy is installed
**** module version_information is installed
The version_information extension is already loaded. To reload it, use:
  %reload_ext version_information
This notebook was generated at 2024-11-23 21:40:58 (대한민국 표준시 = GMT+0900) 
0 Python     3.11.9 64bit [MSC v.1916 64 bit (AMD64)]
1 IPython    8.25.0
2 OS         Windows 10 10.0.26100 SP0
3 numpy      1.26.4
4 pandas     2.2.2
5 matplotlib 3.8.4
6 scipy      1.13.1
7 astropy    6.1.0
8 photutils  1.9.0
9 ccdproc    2.4.2
10 astroscrappy 1.1.0
11 version_information 1.0.4


### import modules

In [53]:
from glob import glob
from pathlib import Path, PosixPath, WindowsPath
import os
from astropy.time import Time
from datetime import datetime, timedelta
from astropy.io import fits
import shutil 

import ysfitsutilpy as yfu
#import ysphotutilpy as ypu
#import ysvisutilpy as yvu

import _astro_utilities
import _Python_utilities

In [ ]:
#%%
#######################################################
# read all files in base directory for processing
# BASEDIR = Path(r"r:\OBS_data")
BASEDIR = Path("/mnt/Rdata/OBS_data") 
# BASEDIR = Path("/Volumes/OBS_data")
 
DOINGDIR = ( BASEDIR/ _astro_utilities.CCD_NEW_dir)
DOINGDIR = ( BASEDIR/ _astro_utilities.CCD_NEWUP_dir)
                
DOINGDIRs = sorted(_Python_utilities.getFullnameListOfallsubDirs(str(DOINGDIR)))
#print ("DOINGDIRs: ", format(DOINGDIRs))
print ("len(DOINGDIRs): ", format(len(DOINGDIRs)))

len(DOINGDIRs):  5


In [55]:
fnameKEYs = ["OBJECT", "IMAGETYP", "FILTER", "DATE-OBS", 
            "EXPOSURE", "OPTIC", "CCDNAME", "CCD-TEMP", "XBINNING"]

In [56]:
for DOINGDIR in DOINGDIRs[:] : 
    DOINGDIR = Path(DOINGDIR)
    print(f"Starting: {str(DOINGDIR.parts[-1])}")
    try: 
        summary = yfu.make_summary(DOINGDIR/"*.fit*",)
        if summary is not None : 
            print("summary: ", summary)
            print("len(summary)", len(summary))
        
            for _, row in summary.iterrows():
                fpath = Path(row["file"])
                print (f"starting {fpath.name}...")
                new_fname = ""
                suffix = ".fit"
                try:
                    for KEY in fnameKEYs :
                        if KEY in ["OBJECT", "IMAGETYP", "FILTER", 
                            "OPTIC", "CCDNAME"] :
                            new_fname += str(row[KEY])+"_"
                        
                        if KEY == "DATE-OBS" : 
                            new_fname += row[KEY][:19].replace("T","-").replace(":","-")+"_"

                        if KEY == "EXPOSURE" : 
                            new_fname += str(int(row[KEY]))+"sec_"

                        if KEY == "CCD-TEMP" : 
                            try:
                                new_fname += str(int(row[KEY]))+"c_"
                            except:
                                new_fname += (row[KEY])+"c_"
                        if KEY == "XBINNING" : 
                            new_fname += str(row[KEY])+"bin"+suffix
                
                    print(new_fname)
                        
                    new_folder = _astro_utilities.get_new_foldername_from_filename(new_fname)
                    #print("new_folder: ", new_folder)
                    new_fpath =  BASEDIR /_astro_utilities.A3_CCD_obs_raw_dir / new_folder / new_fname
                    print("new_fpath: ", new_fpath)

                    if not new_fpath.parents[0].exists():
                        os.makedirs('{0}'.format(str(new_fpath.parents[0])))
                        print('{0} is created'.format(str(new_fpath.parts[-2])))  
                
                    if new_fpath.exists() :
                        duplicate_fpath = BASEDIR / _astro_utilities.CCD_duplicate_dir / new_fpath.name
                        #os.rename(str(new_fpath), str(duplicate_fpath))
                        shutil.move(str(new_fpath), str(duplicate_fpath))
                        print (f"move duplicate file to {str(duplicate_fpath)}")
                    shutil.move(str(fpath), str(new_fpath))
                    print(f"move {str(fpath.name)} to {str(new_fpath)}")


                    # new_fpath =  BASEDIR /_astro_utilities.A3_CCD_obs_raw_dir / new_folder / new_fname
                    # new_fpath_fit =  BASEDIR /_astro_utilities.A3_CCD_obs_raw_dir / new_folder / f'{new_fpath.stem}.fit'
                    # new_fpath_fits =  BASEDIR /_astro_utilities.A3_CCD_obs_raw_dir / new_folder / f'{new_fpath.stem}.fits'
                    # print("new_fpath: ", new_fpath)

                    # if not new_fpath_fit.parents[0].exists():
                    #     os.makedirs('{0}'.format(str(new_fpath_fit.parents[0])))
                    #     print('{0} is created'.format(str(new_fpath_fit.parts[-2])))  
                
                    # if new_fpath_fit.exists() and new_fpath.suffix == '.fits':
                    #     duplicate_fpath = BASEDIR / _astro_utilities.CCD_duplicate_dir / new_fpath_fit.name
                    #     #os.rename(str(new_fpath), str(duplicate_fpath))
                    #     shutil.move(str(new_fpath_fit), str(duplicate_fpath))
                    #     print (f"move duplicate file to {str(duplicate_fpath)}")
                    # if new_fpath_fits.exists() and new_fpath.suffix == '.fits':
                    #     duplicate_fpath = BASEDIR / _astro_utilities.CCD_duplicate_dir / new_fpath.name
                    #     #os.rename(str(new_fpath), str(duplicate_fpath))
                    #     shutil.move(str(fpath), str(duplicate_fpath))
                    #     print (f"move duplicate file to {str(duplicate_fpath)}")
                    # else : 
                    #     #os.rename(str(fpath), str(new_fpath))
                    #     shutil.move(str(fpath), str(new_fpath))
                    #     print(f"move {str(fpath.name)} to {str(new_fpath)}")
                    # shutil.move(str(fpath), str(new_fpath))
                    # print(f"move {str(fpath.name)} to {str(new_fpath)}")
                    
                except Exception as err:
                    print("X"*30, f'\n{err}')
                    #_Python_utilities.write_log(err_log_file, err)
                    pass
    except Exception as err:
        print("X"*30, f'\n{err}')
        #_Python_utilities.write_log(err_log_file, err)
        pass

Starting: 216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin
All 122 keywords (guessed from r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin\216KLEOPATRA_LIGHT_L_2022-10-17-12-34-19_20sec_SVX80T_QSI683ws_-25c_1bin.fit) will be loaded.


C:\Users\Kiehyun\Downloads\ysfitsutilpy\ysfitsutilpy\filemgmt.py:305: UserWarning: Key _TYPE1 not found for r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin\216KLEOPATRA_LIGHT_L_2022-10-17-12-35-00_30sec_SVX80T_QSI683ws_-25c_1bin.fit, filling with None.
  warn(str_keyerror_fill.format(k, str(item)))
C:\Users\Kiehyun\Downloads\ysfitsutilpy\ysfitsutilpy\filemgmt.py:305: UserWarning: Key _TYPE2 not found for r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin\216KLEOPATRA_LIGHT_L_2022-10-17-12-35-00_30sec_SVX80T_QSI683ws_-25c_1bin.fit, filling with None.
  warn(str_keyerror_fill.format(k, str(item)))
C:\Users\Kiehyun\Downloads\ysfitsutilpy\ysfitsutilpy\filemgmt.py:305: UserWarning: Key _UNIT1 not found for r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin\216KLEOPATRA_LIGHT_L_2022-10-17-12-35-00_30sec_SVX80T_QSI683ws_-25c_1bin.fit, filling with None.
  warn(str_k

summary:                                                    file  filesize  SIMPLE  \
0    r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16724160    True   
1    r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
2    r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
3    r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
4    r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
..                                                 ...       ...     ...   
334  r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
335  r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
336  r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
337  r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   
338  r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_...  16666560    True   

     BITPIX  NAXIS  NAXIS1  NAXIS2  EXTEND IMAG

In [57]:
#%%   
#############################################################################
#Check and delete empty folder....
#############################################################################
for i in range(4):
    DOINGDIR = ( BASEDIR/ _astro_utilities.CCD_NEWUP_dir)         
    DOINGDIRs = sorted(_Python_utilities.getFullnameListOfallsubDirs(DOINGDIR))
    #print ("DOINGDIRs: ", format(DOINGDIRs))
    print ("len(DOINGDIRs): ", format(len(DOINGDIRs)))

    for DOINGDIR in DOINGDIRs :    
        if len(os.listdir(str(DOINGDIR))) == 0 :
            shutil.rmtree(f"{str(DOINGDIR)}") # Delete..
            print (f"rmtree {str(DOINGDIR)}")
        else : 
            fpaths = _Python_utilities.getFullnameListOfallFiles(str(DOINGDIR))
            print("fpaths", fpaths)

            for fpath in fpaths[:]:
                print("fpath", fpath)

                if fpath[-4:].lower() in [".txt", "xisf", ".zip", ".png", ".log",
                                            "seal", "tiff", ".axy", "atch", "lved",
                                            "rdls", "xyls", "corr", "xosm", ".ini",
                                            ".wcs", ".csv"] \
                                        and os.path.isfile(fpath):
                    os.remove("{}".format(fpath))
                    print("{} is removed...".format(fpath)) 


len(DOINGDIRs):  5
rmtree r:\OBS_data\A2_CCD_newUpdated_files\216KLEOPATRA_LIGHT_-_2022-10-17_-_SVX80T_QSI683ws_-_1bin/
rmtree r:\OBS_data\A2_CCD_newUpdated_files\NGC7635_LIGHT_-_2024-10-02_-_SVX80T-x80_QSI683ws_-_1bin/
rmtree r:\OBS_data\A2_CCD_newUpdated_files\NGC869_LIGHT_-_2024-10-04_-_SVX80T-x80_QSI683ws_-_1bin/
rmtree r:\OBS_data\A2_CCD_newUpdated_files\Sh2157_LIGHT_-_2024-10-04_-_SVX80T-x80_QSI683ws_-_1bin/
rmtree r:\OBS_data\A2_CCD_newUpdated_files\Skyflat_Flat_-_2024_-_SVX80x80_QSI683ws_-_1bin/
len(DOINGDIRs):  0
len(DOINGDIRs):  0
len(DOINGDIRs):  0
